**Names** Safyre Anderson, Howard Wen , Vamsi Sakhamuri

**Emails** safyre@berkeley.edu, howard.wen1@gmail.com, vamsi@ischool.berkeley.edu 

**Time of Initial Submission:** March 10th, 2016 8am PST

**Section** W261-3, Spring 2016  

**Week** 7 Homework

==========================================================
## ===HW 7.0: Shortest path graph distances (toy networks)===

In this part of your assignment you will develop the base of your code for the week.

Write MRJob classes to find shortest path graph distances, 
as described in the lectures. In addition to finding the distances, 
your code should also output a distance-minimizing path between the source and target.
Work locally for this part of the assignment, and use 
both of the undirected and directed toy networks.

To proof you code's function, run the following jobs

- shortest path in the undirected network from node 1 to node 4
Solution: 1,5,4 

- shortest path in the directed network from node 1 to node 5
Solution: 1,2,4,5

and report your output---make sure it is correct!

=================================

In [141]:
%%writefile shortest_path.py
from mrjob.job import MRJob
from mrjob.step import MRJobStep
import sys
import ast

# This MrJob computes the shortest paths from a single source
#     Mapper: calculate partial gradient for each example  
#     
class shortest_path(MRJob):
    # run before the mapper processes any input. 
    #Adds state and distance information to all the nodes and creates a new file
                
    # Calculate partial gradient for each example 
    def mapper(self, _,line):
        neighbors = []
        edge_info = []
        node = line.split('\t')
        edges = ast.literal_eval(node[1])
        if(node[4]=='Q'):   ##This node is in the frontier, will be expanded
            edge_info = node[1:-1]
            edge_info.append("V")
            yield node[0],edge_info
            for k in edges.keys():
                if(k!='NULL'):
                    neighbors.append([k,edges[k]])
                
            for n in neighbors:
                if(node[3]==' '):
                    path = node[0]
                else:
                    path = node[3]+","+node[0]
                    
                yield n[0],[{'NULL':'NULL'},float(node[2])+1,path,'Q']
        else:
            yield node[0],node[1:]
                  
    def reducer_init(self):
        filename = self.options.pathName+"graph_with_state.txt"
        open(filename,"w").close()
        filenamed = self.options.pathName+"debug.txt"
        open(filenamed,"a+").close()
   
    def reducer(self,key,line):
        filenamed = self.options.pathName+"debug.txt"
        filename = self.options.pathName+"graph_with_state.txt"
        first = True
        visited = False
        queued = False
        unvisited = False

        for l in line:
            debug = []
            for i in l:
                debug.append(str(i))
            with open(filenamed,'a+') as fd:
                fd.writelines(key + "\t" + "\t".join(debug) + "\n")
                    
            if(l[3]==u'Q'):
                if(first==True):
                    shortest_dist = (l[1])
                    first = False
                    shortest_path = l[2]
                else:
                    if(float(shortest_dist)>=float(l[1])):
                        shortest_dist = (l[1])
                        shortest_path = l[2]
                queued = True
            if(l[3]==u'U'):
                edges = str(l[0])
                unvisited = True
                
            if(l[3]==u'V'):
                shortest_dist_V = (l[1])
                shortest_path_V = l[2]
                edges = str(l[0])
                visited = True
            
        if(visited==True):
            if(queued==True):
                if(float(shortest_dist_V) >= float(shortest_dist)):
                    shortest_dist_m = shortest_dist
                    shortest_path_m = shortest_path
                else:
                    shortest_dist_m = shortest_dist_V
                    shortest_path_m = shortest_path_V
            else:
                shortest_dist_m = shortest_dist_V
                shortest_path_m = shortest_path_V
            new_node_info = [edges,str(shortest_dist_m),str(shortest_path_m),'V']
        
        elif(unvisited==True):
            if(queued==True):
                shortest_dist_m = shortest_dist
                shortest_path_m = shortest_path
                new_node_info = [edges,str(shortest_dist_m),str(shortest_path_m),'Q']
            else:
                new_node_info = [str(l[0]),str(l[1]),str(l[2]),'U']               
        
        else:
            new_node_info = [str(l[0]),str(l[1]),str(l[2]),l[3]]

        with open(filename,'a+') as fw:
            fw.writelines(key + "\t" + "\t".join(new_node_info) + "\n")
        yield key,new_node_info
 
    def reducer_final(self):
        filenamed = self.options.pathName+"debug.txt"
        with open(filenamed,"a+") as fd:
            fd.write("Done with an iteration \n")
        
    def configure_options(self):
        super(shortest_path, self).configure_options()
        self.add_passthrough_option(
            '--pathName', dest='pathName', default="", type='str',
            help='pathName: pathname where intermedateResults.txt is stored')
    
    def steps(self):
        return [MRJobStep(mapper=self.mapper,reducer_init=self.reducer_init,reducer=self.reducer,
                        reducer_final=self.reducer_final)] 
    
if __name__ == '__main__':
    shortest_path.run()

Overwriting shortest_path.py


In [142]:
!rm graph_with_state.txt

In [143]:
%reload_ext autoreload
%autoreload 2

from numpy import random,array
from shortest_path import shortest_path
import sys

first = True

fa = 'directed_toy.txt'
fb = 'graph_with_state.txt'

#Transforming the directed_toy.txt to included state,distance,path information
with open(fa, 'r') as fr:
    for f in fr:
        adj_list = []
        adjl = f.strip().split('\t')
        if(first==True):
            adj_list.append(adjl[0]) #Node
            adj_list.append(adjl[1]) #Edges and Weights
            adj_list.append(str(0))  #Shortest Distance
            adj_list.append(' ')    #Shortest Path          
            adj_list.append('Q')     #state
            first=False
        else:
            adj_list.append(adjl[0])         #Node
            adj_list.append(adjl[1])         #Edges and Weights
            adj_list.append(str(sys.maxint)) #Shortest Distance
            adj_list.append(' ')            #Shortest Path
            adj_list.append('U')             #state
        
        with open(fb,'a+') as fw:
            fw.writelines('\t'.join(adj_list)+'\n')

mr_job = shortest_path(args=[fb,'--pathName','/Users/Vamsi/Documents/W261/hw7/']) 

i = 1
while(1):
    print "\n","iteration ",i,"\n"
    unvisited_nodes = 0
    with mr_job.make_runner() as runner: 
        runner.run()
        # stream_output: get access of the output 
        for line in runner.stream_output():
            key,value =  mr_job.parse_output_line(line)
            print key,value
            if(value[3]!=u'V'):
                unvisited_nodes = unvisited_nodes + 1
            
    if(unvisited_nodes==0):
        break
    i +=1

print "Done- All nodes have been visited"
            


iteration  1 

1

 [u"{'2': 1, '6': 1}", u'0', u' ', u'V']
2 [u"{'1': 1, '3': 1, '4': 1}", u'1.0', u'1', u'Q']
3 [u"{'2': 1, '4': 1}", u'9223372036854775807', u' ', u'U']
4 [u"{'2': 1, '5': 1}", u'9223372036854775807', u' ', u'U']
5 [u"{'1': 1, '2': 1, '4': 1}", u'9223372036854775807', u' ', u'U']
6 [u"{u'NULL': u'NULL'}", u'1.0', u'1', u'Q']

iteration  2 

1

 [u"{'2': 1, '6': 1}", u'0', u' ', u'V']
2 [u"{'1': 1, '3': 1, '4': 1}", u'1.0', u'1', u'V']
3 [u"{'2': 1, '4': 1}", u'2.0', u'1,2', u'Q']
4 [u"{'2': 1, '5': 1}", u'2.0', u'1,2', u'Q']
5 [u"{'1': 1, '2': 1, '4': 1}", u'9223372036854775807', u' ', u'U']
6 [u"{u'NULL': u'NULL'}", u'1.0', u'1', u'V']

iteration  3 

1

 [u"{'2': 1, '6': 1}", u'0', u' ', u'V']
2 [u"{'1': 1, '3': 1, '4': 1}", u'1.0', u'1', u'V']
3 [u"{'2': 1, '4': 1}", u'2.0', u'1,2', u'V']
4 [u"{'2': 1, '5': 1}", u'2.0', u'1,2', u'V']
5 [u"{'1': 1, '2': 1, '4': 1}", u'3.0', u'1,2,4', u'Q']
6 [u"{u'NULL': u'NULL'}", u'1.0', u'1', u'V']

iteration  4 

1 [u"{'2': 1, '6': 1}", u'0', u' ', u'V']
2 [u"{'1': 1, '3': 1, '4': 1}", u'1.0', u'1', u'V']
3 [u"{'2': 1, '4': 1}", u'2.0', u'1,2', u'V']
4 [u"{'2': 1, '5': 1}", u'2.0', u'1,2', u'V']
5 [u"{'1': 1, '2': 1, '4': 1}", u'3.0', u'1,2,4', u'V']
6 [u"{u'NULL': u'NULL'}", u'1.0', u'1', u'V']
Done- All nodes have been visited


In [144]:
!rm graph_with_state.txt

In [145]:
%reload_ext autoreload
%autoreload 2

from numpy import random,array
from shortest_path import shortest_path
import sys

first = True

fa = 'undirected_toy.txt'
fb = 'graph_with_state.txt'

#Transforming the directed_toy.txt to included state,distance,path information
with open(fa, 'r') as fr:
    for f in fr:
        adj_list = []
        adjl = f.strip().split('\t')
        if(first==True):
            adj_list.append(adjl[0]) #Node
            adj_list.append(adjl[1]) #Edges and Weights
            adj_list.append(str(0))  #Shortest Distance
            adj_list.append(' ')    #Shortest Path          
            adj_list.append('Q')     #state
            first=False
        else:
            adj_list.append(adjl[0])         #Node
            adj_list.append(adjl[1])         #Edges and Weights
            adj_list.append(str(sys.maxint)) #Shortest Distance
            adj_list.append(' ')            #Shortest Path
            adj_list.append('U')             #state
        
        with open(fb,'a+') as fw:
            fw.writelines('\t'.join(adj_list)+'\n')

mr_job = shortest_path(args=[fb,'--pathName','/Users/Vamsi/Documents/W261/hw7/']) 

i = 1
while(1):
    print "\n","iteration ",i,"\n"
    unvisited_nodes = 0
    with mr_job.make_runner() as runner: 
        runner.run()
        # stream_output: get access of the output 
        for line in runner.stream_output():
            key,value =  mr_job.parse_output_line(line)
            print key,value
            if(value[3]!=u'V'):
                unvisited_nodes = unvisited_nodes + 1
            
    if(unvisited_nodes==0):
        break
    i +=1

print "Done- All nodes have been visited"


iteration  1 

1 [u"{'2': 1,'5': 1}", u'0', u' ', u'V']
2 [u"{'1': 1,'3': 1,'4': 1,'5': 1}", u'1.0', u'1', u'Q']
3 [u"{'2': 1, '4': 1}", u'9223372036854775807', u' ', u'U']
4 [u"{'2': 1,'3': 1,'5': 1}", u'9223372036854775807', u' ', u'U']
5 [u"{'1': 1, '2': 1, '4': 1}", u'1.0', u'1', u'Q']

iteration  2 

1

 [u"{'2': 1,'5': 1}", u'0', u' ', u'V']
2 [u"{'1': 1,'3': 1,'4': 1,'5': 1}", u'1.0', u'1', u'V']
3 [u"{'2': 1, '4': 1}", u'2.0', u'1,2', u'Q']
4 [u"{'2': 1,'3': 1,'5': 1}", u'2.0', u'1,5', u'Q']
5 [u"{'1': 1, '2': 1, '4': 1}", u'1.0', u'1', u'V']

iteration  3 

1 [u"{'2': 1,'5': 1}", u'0', u' ', u'V']
2 [u"{'1': 1,'3': 1,'4': 1,'5': 1}", u'1.0', u'1', u'V']
3 [u"{'2': 1, '4': 1}", u'2.0', u'1,2', u'V']
4 [u"{'2': 1,'3': 1,'5': 1}", u'2.0', u'1,5', u'V']
5 [u"{'1': 1, '2': 1, '4': 1}", u'1.0', u'1', u'V']
Done- All nodes have been visited


In [ ]:
!aws s3 ls

In [ ]:
!aws s3 ls s3://ucb-mids-mls-networks/synNet/synNet.txt

In [ ]:
!aws s3 cp s3://ucb-mids-mls-networks/synNet/synNet.txt /Users/Vamsi

## =================================
## ==Main dataset 1: NLTK synonyms==

In the next part of this assignment you will explore a network derived from
the NLTK synonym database used for evaluation in HW 5. At a high level, this
network is undirected, defined so that there exists link between two nodes/words 
if the pair or words are a synonym. These data may be found at the location:

s3://ucb-mids-mls-networks/synNet/synNet.txt  
s3://ucb-mids-mls-networks/synNet/indices.txt
On under the Data Subfolder for HW7 on Dropbox with the same file names

where synNet.txt contains a sparse representation of the network:

(index) \t (dictionary of links)

in indexed form, and indices.txt contains a lookup list

(word) \t (index)

of indices and words. This network is small enough for you to explore and run
scripts locally, but will also be good for a systems test (for later) on AWS.

In the dictionary, target nodes are keys, link weights are values 
(here, all weights are 1, i.e., the network is unweighted).


## =======================================================
## ===HW 7.1: Exploratory data analysis (NLTK synonyms)===

Using MRJob, explore the synonyms network data.
Consider plotting the degree distribution (does it follow a power law?),
and determine some of the key features, like:

number of nodes,  
number links,  
or the average degree (i.e., the average number of links per node),  
etc...  

As you develop your code, please be sure to run it locally first (though on the whole dataset). 
Once you have gotten you code to run locally, deploy it on AWS as a systems test
in preparation for our next dataset (which will require AWS).

In [ ]:
%%writefile nltk_stats.py
from mrjob.job import MRJob
from mrjob.step import MRJobStep
import sys
import ast

# This MrJob computes the shortest paths from a single source
#     Mapper: calculate partial gradient for each example  
#     
class nltk_stats(MRJob):
    # run before the mapper processes any input. 
    #Adds state and distance information to all the nodes and creates a new file
                
    # Calculate partial gradient for each example 
    def mapper(self, _,line):
        total = line.split('\t')
        node = total[0]
        edge = total[1]
        edges = ast.literal_eval(edge)       
        yield node,len(edges)
    
    def reducer(self,key,value):
        for v in value:
            yield key,v
        
    def steps(self):
        return [MRJobStep(mapper=self.mapper,reducer=self.reducer)] 
    
if __name__ == '__main__':
    nltk_stats.run()

In [ ]:
!python nltk_stats.py -r emr s3://hw7-ml261/

In [ ]:
%reload_ext autoreload
%autoreload 2

from numpy import random,array
from nltk_stats import nltk_stats
import sys

#mr_job = nltk_stats(args=['synNet.txt','--pathName','/Users/Vamsi/Documents/W261/hw7/']) 
mr_job = nltk_stats(args=['s3://hw7-ml261/synNet.txt','-r','emr'])

total_nodes = 0
total_links = 0
num_links_acc = []
with mr_job.make_runner() as runner: 
    runner.run()
    # stream_output: get access of the output 
    for line in runner.stream_output():
        node,num_links =  mr_job.parse_output_line(line)
        total_nodes = total_nodes+1
        total_links = total_links+int(num_links)
        num_links_acc.append([float(node),num_links])

avg_degree = total_links/float(total_nodes)

print "Total number of nodes in the graph is : ",total_nodes
print "Average degree (total_links/total_nodes) of the graph is : ",avg_degree
print "Total number of links/edges in the graph are : ",total_links/2

In [ ]:
%matplotlib inline

In [ ]:
#Plot
import numpy as np
import matplotlib.pyplot as plt

num_links_acc = np.array(num_links_acc)
sorted_link_count = np.sort(num_links_acc[:,1])
plt.plot(sorted_link_count)
plt.ylabel("Number of edges")
plt.xlabel("Any given node")
plt.show()

Yes, the degree distribution (number of edges) follows a square law.

Testing AWS

In [ ]:
!aws s3 mb s3://hw7-ml261/

In [ ]:
!aws s3 ls 

In [ ]:
!aws s3 cp synNet.txt s3://hw7-ml261

### ===========================================================
### ===HW 7.2: Shortest path graph distances (NLTK synonyms)===

Write (reuse your code from 7.0) an MRJob class to find shortest path graph distances, 
and apply it to the NLTK synonyms network dataset. 

Proof your code's function by running the job:

- shortest path starting at "walk" (index=7827) and ending at "make" (index=536),

and showing you code's output. Once again, your output should include the path and the distance.

As you develop your code, please be sure to run it locally first (though on the whole dataset). 
Once you have gotten you code to run locally, deploy it on AWS as a systems test
in preparation for our next dataset (which will require AWS).

In [151]:
%%writefile shortest_path_nltk.py
from mrjob.job import MRJob
from mrjob.step import MRJobStep
import sys
import ast

# This MrJob computes the shortest paths from a single source
#     Mapper: calculate partial gradient for each example  
#     
class shortest_path_nltk(MRJob):
    # run before the mapper processes any input. 
    #Adds state and distance information to all the nodes and creates a new file
                
    # Calculate partial gradient for each example 
    def mapper(self, _,line):
        neighbors = []
        edge_info = []
        node = line.split('\t')
        edges = ast.literal_eval(node[1])
        if(node[4]=='Q'):   ##This node is in the frontier, will be expanded
            edge_info = node[1:-1]
            edge_info.append("V")
            yield node[0],edge_info
            for k in edges.keys():
                if(k!='NULL'):
                    neighbors.append([k,edges[k]])
                
            for n in neighbors:
                if(node[3]==' '):
                    path = node[0]
                else:
                    path = node[3]+","+node[0]
                    
                yield n[0],[{'NULL':'NULL'},float(node[2])+1,path,'Q']
        else:
            yield node[0],node[1:]
                  
    def reducer_init(self):
        filename = self.options.pathName+"graph_with_state.txt"
        open(filename,"w").close()
        filenamed = self.options.pathName+"debug.txt"
        open(filenamed,"a+").close()
   
    def reducer(self,key,line):
        filenamed = self.options.pathName+"debug.txt"
        filename = self.options.pathName+"graph_with_state.txt"
        first = True
        visited = False
        queued = False
        unvisited = False

        for l in line:
            debug = []
            for i in l:
                debug.append(str(i))
            with open(filenamed,'a+') as fd:
                fd.writelines(key + "\t" + "\t".join(debug) + "\n")
                    
            if(l[3]==u'Q'):
                if(first==True):
                    shortest_dist = (l[1])
                    first = False
                    shortest_path = l[2]
                else:
                    if(float(shortest_dist)>=float(l[1])):
                        shortest_dist = (l[1])
                        shortest_path = l[2]
                queued = True
            if(l[3]==u'U'):
                edges = str(l[0])
                unvisited = True
                
            if(l[3]==u'V'):
                shortest_dist_V = (l[1])
                shortest_path_V = l[2]
                edges = str(l[0])
                visited = True
            
        if(visited==True):
            if(queued==True):
                if(float(shortest_dist_V) >= float(shortest_dist)):
                    shortest_dist_m = shortest_dist
                    shortest_path_m = shortest_path
                else:
                    shortest_dist_m = shortest_dist_V
                    shortest_path_m = shortest_path_V
            else:
                shortest_dist_m = shortest_dist_V
                shortest_path_m = shortest_path_V
            new_node_info = [edges,str(shortest_dist_m),str(shortest_path_m),'V']
        
        elif(unvisited==True):
            if(queued==True):
                shortest_dist_m = shortest_dist
                shortest_path_m = shortest_path
                new_node_info = [edges,str(shortest_dist_m),str(shortest_path_m),'Q']
            else:
                new_node_info = [str(l[0]),str(l[1]),str(l[2]),'U']               
        
        else:
            new_node_info = [str(l[0]),str(l[1]),str(l[2]),l[3]]

        with open(filename,'a+') as fw:
            fw.writelines(key + "\t" + "\t".join(new_node_info) + "\n")
        yield key,new_node_info
 
    def reducer_final(self):
        filenamed = self.options.pathName+"debug.txt"
        with open(filenamed,"a+") as fd:
            fd.write("Done with an iteration \n")
        
    def configure_options(self):
        super(shortest_path_nltk, self).configure_options()
        self.add_passthrough_option(
            '--pathName', dest='pathName', default="", type='str',
            help='pathName: pathname where intermedateResults.txt is stored')
    
    def steps(self):
        return [MRJobStep(mapper=self.mapper,reducer_init=self.reducer_init,reducer=self.reducer,
                        reducer_final=self.reducer_final)] 
    
if __name__ == '__main__':
    shortest_path_nltk.run()

Overwriting shortest_path_nltk.py


In [1]:
!rm graph_with_state.txt

rm: graph_with_state.txt: No such file or directory


In [ ]:
%reload_ext autoreload
%autoreload 2

from numpy import random,array
from shortest_path_nltk import shortest_path_nltk
import sys

fa = 'synNet.txt'
fb = 'graph_with_state.txt'

#Transforming the directed_toy.txt to included state,distance,path information
with open(fa, 'r') as fr:
    for f in fr:
        adj_list = []
        adjl = f.strip().split('\t')
        if(adjl[0]==u'7827'):
            adj_list.append(adjl[0]) #Node
            adj_list.append(adjl[1]) #Edges and Weights
            adj_list.append(str(0))  #Shortest Distance
            adj_list.append(' ')    #Shortest Path          
            adj_list.append('Q')     #state
            first=False
        else:
            adj_list.append(adjl[0])         #Node
            adj_list.append(adjl[1])         #Edges and Weights
            adj_list.append(str(sys.maxint)) #Shortest Distance
            adj_list.append(' ')            #Shortest Path
            adj_list.append('U')             #state
        
        with open(fb,'a+') as fw:
            fw.writelines('\t'.join(adj_list)+'\n')

mr_job = shortest_path(args=[fb,'--pathName','/Users/Vamsi/Documents/W261/hw7/']) 

i = 1
while(1):
    print "\n","iteration ",i,"\n"
    unvisited_nodes = 0
    with mr_job.make_runner() as runner: 
        runner.run()
        # stream_output: get access of the output 
        for line in runner.stream_output():
            key,value =  mr_job.parse_output_line(line)
            print key,value
            if(value[3]!=u'V'):
                unvisited_nodes = unvisited_nodes + 1
            
    if(unvisited_nodes==0):
        break
    i +=1

print "Done- All nodes have been visited"


iteration  1 

1 [u"{'2': 1, '3': 1, '4': 1}", u'9223372036854775807', u' ', u'U']
10 [u"{'11': 1, '12': 1, '13': 1, '14': 1, '15': 1, '16': 1, '17': 1}", u'9223372036854775807', u' ', u'U']
100 [u"{'92': 1, '2870': 1, '3122': 1, '2871': 1, '93': 1, '3827': 1, '617': 1, '5336': 1, '2441': 1, '5550': 1, '2872': 1, '2873': 1, '2874': 1, '2443': 1, '2875': 1, '3720': 1, '3722': 1, '360': 1, '4647': 1}", u'9223372036854775807', u' ', u'U']
1000 [u"{'997': 1, '999': 1, '1001': 1, '1002': 1, '1003': 1, '1004': 1}", u'9223372036854775807', u' ', u'U']
1001 [u"{'997': 1, '998': 1, '999': 1, '1000': 1}", u'9223372036854775807', u' ', u'U']
1002 [u"{'997': 1, '998': 1, '999': 1, '1000': 1}", u'9223372036854775807', u' ', u'U']
1003 [u"{'997': 1, '998': 1, '2095': 1, '999': 1, '1000': 1}", u'9223372036854775807', u' ', u'U']
1004 [u"{'997': 1, '998': 1, '3352': 1, '999': 1, '1000': 1}", u'9223372036854775807', u' ', u'U']
1005 [u"{'948': 1, '1006': 1}", u'9223372036854775807', u' ', u'U']
1006 [


921 [u"{'918': 1, '2881': 1, '2883': 1, '919': 1, '920': 1, '2885': 1, '887': 1, '8021': 1, '2882': 1}", u'9223372036854775807', u' ', u'U']
922 [u"{'923': 1, '924': 1}", u'9223372036854775807', u' ', u'U']
923 [u"{'922': 1, '924': 1}", u'9223372036854775807', u' ', u'U']
924 [u"{'922': 1, '923': 1, '1254': 1, '6275': 1}", u'9223372036854775807', u' ', u'U']
925 [u"{'926': 1, '927': 1}", u'9223372036854775807', u' ', u'U']
926 [u"{'925': 1, '927': 1}", u'9223372036854775807', u' ', u'U']
927 [u"{'925': 1, '926': 1}", u'9223372036854775807', u' ', u'U']
928 [u"{'929': 1, '930': 1, '108': 1, '931': 1, '111': 1, '112': 1}", u'9223372036854775807', u' ', u'U']
929 [u"{'928': 1, '2602': 1, '2605': 1, '2890': 1, '2892': 1, '3487': 1, '930': 1, '2604': 1, '1208': 1, '2266': 1, '4533': 1, '56': 1, '3687': 1, '1913': 1, '4797': 1, '3491': 1, '3492': 1}", u'9223372036854775807', u' ', u'U']
93 [u"{'92': 1, '1084': 1, '2870': 1, '3144': 1, '3826': 1, '3827': 1, '3828': 1, '94': 1, '3829': 1, '38

 [u"{'823': 1, '275': 1}", u'9223372036854775807', u' ', u'U']
8240 [u"{'8239': 1}", u'9223372036854775807', u' ', u'U']
8241 [u"{'8242': 1, '8243': 1}", u'9223372036854775807', u' ', u'U']
8242 [u"{'8241': 1, '8243': 1}", u'9223372036854775807', u' ', u'U']
8243 [u"{'8241': 1, '8242': 1}", u'9223372036854775807', u' ', u'U']
8244 [u"{'8245': 1}", u'9223372036854775807', u' ', u'U']
8245 [u"{'8244': 1}", u'9223372036854775807', u' ', u'U']
8246 [u"{'3413': 1}", u'9223372036854775807', u' ', u'U']
8247 [u"{'8248': 1}", u'9223372036854775807', u' ', u'U']
8248 [u"{'8247': 1}", u'9223372036854775807', u' ', u'U']
8249 [u"{'3752': 1}", u'9223372036854775807', u' ', u'U']
825 [u"{'823': 1, '275': 1, '5615': 1}", u'9223372036854775807', u' ', u'U']
8250 [u"{'8251': 1}", u'9223372036854775807', u' ', u'U']
8251 [u"{'8250': 1}", u'9223372036854775807', u' ', u'U']
8252 [u"{'4749': 1}", u'9223372036854775807', u' ', u'U']
8253 [u"{'7827': 1}", u'1.0', u'7827', u'V']
8254 [u"{'7827': 1, '7828': 


8208 [u"{'8207': 1}", u'9223372036854775807', u' ', u'U']
8209 [u"{'3339': 1, '2848': 1}", u'9223372036854775807', u' ', u'U']
821 [u"{'813': 1, '3122': 1, '816': 1, '4153': 1, '3123': 1, '5694': 1, '360': 1, '4647': 1, '8092': 1}", u'9223372036854775807', u' ', u'U']
8210 [u"{'7912': 1}", u'9223372036854775807', u' ', u'U']
8211 [u"{'3365': 1}", u'9223372036854775807', u' ', u'U']
8212 [u"{'8213': 1}", u'9223372036854775807', u' ', u'U']
8213 [u"{'8212': 1}", u'9223372036854775807', u' ', u'U']
8214 [u"{'8215': 1}", u'9223372036854775807', u' ', u'U']
8215 [u"{'8214': 1}", u'9223372036854775807', u' ', u'U']
8216 [u"{'8217': 1}", u'9223372036854775807', u' ', u'U']
8217 [u"{'8216': 1}", u'9223372036854775807', u' ', u'U']
8218 [u"{'8219': 1}", u'9223372036854775807', u' ', u'U']
8219 [u"{'8218': 1}", u'9223372036854775807', u' ', u'U']
822 [u"{'813': 1, '823': 1, '2509': 1, '3803': 1, '3804': 1, '3805': 1, '3806': 1, '2295': 1, '814': 1, '4150': 1, '4151': 1, '4152': 1, '816': 1, '41